# Create NHL SQLite Database

This notebook creates a relational SQLite database from the collected NHL data.

## Database Schema:
- **players**: Player biographical information (both skaters and goalies)
- **teams**: Team information
- **seasons**: Season metadata
- **skater_seasons**: Skater statistics for each season (many-to-many)
- **goalie_seasons**: Goalie statistics for each season (many-to-many)
- **player_teams**: Player-team relationships by season (many-to-many)
- **team_standings**: Team performance by season

In [1]:
# Import required libraries
import sqlite3
import json
import pandas as pd
from pathlib import Path
from datetime import datetime
import warnings
warnings.filterwarnings('ignore')

# Import custom modules
from config import config
from process_data import get_season_teams, get_all_player_ids, load_player
from player import Player

print("✅ Libraries imported successfully!")

✅ Libraries imported successfully!


## 1. Configuration

In [2]:
# Database configuration
DB_NAME = 'nhl_data.db'
SEASONS = config.data.training_seasons  # From config.py

print(f"Database: {DB_NAME}")
print(f"Seasons to process: {SEASONS}")

Database: nhl_data.db
Seasons to process: ['20002001', '20012002', '20022003', '20032004', '20042005', '20052006', '20062007', '20072008', '20082009', '20092010', '20102011', '20112012', '20122013', '20132014', '20142015', '20152016', '20162017', '20172018', '20182019', '20192020', '20202021', '20212022', '20222023', '20232024', '20242025', '20252026']


## 2. Create Database Schema

In [3]:
def create_database_schema(db_path):
    """
    Create the database schema with all tables and relationships.
    Skaters and goalies have separate season tables for their specific stats.
    """
    conn = sqlite3.connect(db_path)
    cursor = conn.cursor()
    
    # Drop existing tables (if recreating)
    cursor.execute("DROP TABLE IF EXISTS player_teams")
    cursor.execute("DROP TABLE IF EXISTS skater_seasons")
    cursor.execute("DROP TABLE IF EXISTS goalie_seasons")
    cursor.execute("DROP TABLE IF EXISTS team_standings")
    cursor.execute("DROP TABLE IF EXISTS players")
    cursor.execute("DROP TABLE IF EXISTS teams")
    cursor.execute("DROP TABLE IF EXISTS seasons")
    
    # Create players table (both skaters and goalies)
    cursor.execute('''
    CREATE TABLE players (
        player_id INTEGER PRIMARY KEY,
        first_name TEXT,
        last_name TEXT,
        full_name TEXT,
        position TEXT,
        role TEXT CHECK(role IN ('A', 'D', 'G')),
        birth_date TEXT,
        age INTEGER,
        height INTEGER,
        weight INTEGER,
        country TEXT,
        salary INTEGER,
        created_at TIMESTAMP DEFAULT CURRENT_TIMESTAMP
    )
    ''')
    
    # Create teams table
    cursor.execute('''
    CREATE TABLE teams (
        team_id INTEGER PRIMARY KEY AUTOINCREMENT,
        team_abbrev TEXT UNIQUE NOT NULL,
        team_name TEXT,
        created_at TIMESTAMP DEFAULT CURRENT_TIMESTAMP
    )
    ''')
    
    # Create seasons table
    cursor.execute('''
    CREATE TABLE seasons (
        season_id TEXT PRIMARY KEY,
        start_year INTEGER,
        end_year INTEGER,
        created_at TIMESTAMP DEFAULT CURRENT_TIMESTAMP
    )
    ''')
    
    # Create skater_seasons table (many-to-many: skater stats per season)
    cursor.execute('''
    CREATE TABLE skater_seasons (
        id INTEGER PRIMARY KEY AUTOINCREMENT,
        player_id INTEGER,
        season_id TEXT,
        games_played INTEGER,
        goals INTEGER,
        assists INTEGER,
        points INTEGER,
        plus_minus INTEGER,
        penalty_minutes INTEGER,
        shots INTEGER,
        shooting_pct REAL,
        time_on_ice_per_game REAL,
        powerplay_goals INTEGER,
        powerplay_points INTEGER,
        shorthanded_goals INTEGER,
        shorthanded_points INTEGER,
        game_winning_goals INTEGER,
        overtime_goals INTEGER,
        faceoff_pct REAL,
        avg_shifts_per_game REAL,
        -- Derived metrics
        ppg REAL,  -- Points per game
        goals_per_game REAL,
        assists_per_game REAL,
        shots_per_game REAL,
        marqueur_points REAL,
        marqueur_ppg REAL,
        FOREIGN KEY (player_id) REFERENCES players(player_id),
        FOREIGN KEY (season_id) REFERENCES seasons(season_id),
        UNIQUE(player_id, season_id)
    )
    ''')

    # Create goalie_seasons table (many-to-many: goalie stats per season)
    cursor.execute('''
    CREATE TABLE goalie_seasons (
        id INTEGER PRIMARY KEY AUTOINCREMENT,
        player_id INTEGER,
        season_id TEXT,
        games_played INTEGER,
        games_started INTEGER,
        wins INTEGER,
        losses INTEGER,
        ties INTEGER,
        overtime_losses INTEGER,
        shutouts INTEGER,
        goals_against INTEGER,
        goals_against_avg REAL,
        shots_against INTEGER,
        saves INTEGER,
        save_pct REAL,
        time_on_ice REAL,
        penalty_minutes INTEGER,
        -- Additional goalie metrics
        goals INTEGER,  -- Rare but some goalies score
        assists INTEGER,
        points INTEGER,
        -- Derived metrics
        wins_per_game REAL,
        shutout_pct REAL,
        FOREIGN KEY (player_id) REFERENCES players(player_id),
        FOREIGN KEY (season_id) REFERENCES seasons(season_id),
        UNIQUE(player_id, season_id)
    )
    ''')
    
    # Create player_teams table (many-to-many: player-team assignments)
    cursor.execute('''
    CREATE TABLE player_teams (
        id INTEGER PRIMARY KEY AUTOINCREMENT,
        player_id INTEGER,
        team_id INTEGER,
        season_id TEXT,
        FOREIGN KEY (player_id) REFERENCES players(player_id),
        FOREIGN KEY (team_id) REFERENCES teams(team_id),
        FOREIGN KEY (season_id) REFERENCES seasons(season_id),
        UNIQUE(player_id, team_id, season_id)
    )
    ''')
    
    # Create team_standings table
    cursor.execute('''
    CREATE TABLE team_standings (
        id INTEGER PRIMARY KEY AUTOINCREMENT,
        team_id INTEGER,
        season_id TEXT,
        games_played INTEGER,
        wins INTEGER,
        losses INTEGER,
        overtime_losses INTEGER,
        points INTEGER,
        points_pct REAL,
        goals_for INTEGER,
        goals_against INTEGER,
        goal_differential INTEGER,
        FOREIGN KEY (team_id) REFERENCES teams(team_id),
        FOREIGN KEY (season_id) REFERENCES seasons(season_id),
        UNIQUE(team_id, season_id)
    )
    ''')
    
    # Create indexes for better query performance
    cursor.execute('CREATE INDEX idx_skater_seasons_player ON skater_seasons(player_id)')
    cursor.execute('CREATE INDEX idx_skater_seasons_season ON skater_seasons(season_id)')
    cursor.execute('CREATE INDEX idx_goalie_seasons_player ON goalie_seasons(player_id)')
    cursor.execute('CREATE INDEX idx_goalie_seasons_season ON goalie_seasons(season_id)')
    cursor.execute('CREATE INDEX idx_player_teams_player ON player_teams(player_id)')
    cursor.execute('CREATE INDEX idx_player_teams_team ON player_teams(team_id)')
    cursor.execute('CREATE INDEX idx_player_teams_season ON player_teams(season_id)')
    
    conn.commit()
    conn.close()
    
    print("✅ Database schema created successfully!")

# Create the database
create_database_schema(DB_NAME)

print(f"\n📊 Database '{DB_NAME}' created with the following tables:")
print("  - players (both skaters and goalies)")
print("  - teams")
print("  - seasons")
print("  - skater_seasons (skater stats per season)")
print("  - goalie_seasons (goalie stats per season)")
print("  - player_teams (player-team relationships)")
print("  - team_standings (team performance per season)")

✅ Database schema created successfully!

📊 Database 'nhl_data.db' created with the following tables:
  - players (both skaters and goalies)
  - teams
  - seasons
  - skater_seasons (skater stats per season)
  - goalie_seasons (goalie stats per season)
  - player_teams (player-team relationships)
  - team_standings (team performance per season)


## 3. Populate Seasons Table

In [4]:
def populate_seasons(db_path, seasons):
    """
    Populate the seasons table
    """
    conn = sqlite3.connect(db_path)
    cursor = conn.cursor()
    
    for season in seasons:
        start_year = int(season[:4])
        end_year = int(season[4:])
        
        cursor.execute('''
        INSERT OR IGNORE INTO seasons (season_id, start_year, end_year)
        VALUES (?, ?, ?)
        ''', (season, start_year, end_year))
    
    conn.commit()
    conn.close()
    
    print(f"✅ Added {len(seasons)} seasons to database")

populate_seasons(DB_NAME, SEASONS)

# Verify
conn = sqlite3.connect(DB_NAME)
df_seasons = pd.read_sql_query("SELECT * FROM seasons", conn)
conn.close()
print("\n📋 Seasons in database:")
print(df_seasons)

✅ Added 26 seasons to database

📋 Seasons in database:
   season_id  start_year  end_year           created_at
0   20002001        2000      2001  2025-10-07 03:42:52
1   20012002        2001      2002  2025-10-07 03:42:52
2   20022003        2002      2003  2025-10-07 03:42:52
3   20032004        2003      2004  2025-10-07 03:42:52
4   20042005        2004      2005  2025-10-07 03:42:52
5   20052006        2005      2006  2025-10-07 03:42:52
6   20062007        2006      2007  2025-10-07 03:42:52
7   20072008        2007      2008  2025-10-07 03:42:52
8   20082009        2008      2009  2025-10-07 03:42:52
9   20092010        2009      2010  2025-10-07 03:42:52
10  20102011        2010      2011  2025-10-07 03:42:52
11  20112012        2011      2012  2025-10-07 03:42:52
12  20122013        2012      2013  2025-10-07 03:42:52
13  20132014        2013      2014  2025-10-07 03:42:52
14  20142015        2014      2015  2025-10-07 03:42:52
15  20152016        2015      2016  2025-10-07 03

## 4. Populate Teams Table

In [5]:
def populate_teams(db_path, seasons):
    """
    Populate the teams table from all seasons
    """
    conn = sqlite3.connect(db_path)
    cursor = conn.cursor()
    
    teams_added = set()
    
    for season in seasons:
        try:
            teams = get_season_teams(season)
            
            for team_abbrev in teams:
                if team_abbrev not in teams_added:
                    cursor.execute('''
                    INSERT OR IGNORE INTO teams (team_abbrev, team_name)
                    VALUES (?, ?)
                    ''', (team_abbrev, team_abbrev))  # TODO: Replace team_name with full name if available and add scrape_salaries name
                    teams_added.add(team_abbrev)
        
        except Exception as e:
            print(f"⚠️  Warning: Could not get teams for {season}: {e}")
    
    conn.commit()
    conn.close()
    
    print(f"✅ Added {len(teams_added)} teams to database")
    return teams_added

teams = populate_teams(DB_NAME, SEASONS)

# Verify
conn = sqlite3.connect(DB_NAME)
df_teams = pd.read_sql_query("SELECT * FROM teams ORDER BY team_abbrev", conn)
conn.close()
print(f"\n📋 Teams in database ({len(df_teams)}):")
print(df_teams.head(10))

2025-10-06 23:42:52,626 - INFO - Player points data for 20002001 already exists, skipping download
2025-10-06 23:42:52,628 - INFO - Found 30 teams for season 20002001: ['PIT', 'COL', 'NJD', 'BOS', 'FLA', 'EDM', 'LAK', 'OTT', 'DAL', 'STL', 'WSH', 'BUF', 'NYR', 'PHI', 'DET', 'PHX', 'ATL', 'VAN', 'CHI', 'TOR', 'SJS', 'CGY', 'CAR', 'ANA', 'NYI', 'TBL', 'NSH', 'CBJ', 'MTL', 'MIN']
2025-10-06 23:42:52,628 - INFO - Player points data for 20012002 already exists, skipping download
2025-10-06 23:42:52,628 - INFO - Found 30 teams for season 20012002: ['CGY', 'VAN', 'TOR', 'WSH', 'COL', 'STL', 'PHI', 'DAL', 'CAR', 'PIT', 'DET', 'NYI', 'LAK', 'NYR', 'BUF', 'BOS', 'OTT', 'CHI', 'MIN', 'ATL', 'SJS', 'PHX', 'TBL', 'NJD', 'CBJ', 'EDM', 'ANA', 'MTL', 'FLA', 'NSH']
2025-10-06 23:42:52,628 - INFO - Player points data for 20022003 already exists, skipping download
2025-10-06 23:42:52,637 - INFO - Found 30 teams for season 20022003: ['COL', 'VAN', 'BOS', 'STL', 'PIT', 'ATL', 'LAK', 'DAL', 'DET', 'ANA', 'OT

✅ Added 35 teams to database

📋 Teams in database (35):
   team_id team_abbrev team_name           created_at
0       24         ANA       ANA  2025-10-07 03:42:52
1       32         ARI       ARI  2025-10-07 03:42:56
2       17         ATL       ATL  2025-10-07 03:42:52
3        4         BOS       BOS  2025-10-07 03:42:52
4       12         BUF       BUF  2025-10-07 03:42:52
5       23         CAR       CAR  2025-10-07 03:42:52
6       28         CBJ       CBJ  2025-10-07 03:42:52
7       22         CGY       CGY  2025-10-07 03:42:52
8       19         CHI       CHI  2025-10-07 03:42:52
9        2         COL       COL  2025-10-07 03:42:52


## 5. Populate Players and Player Data

In [6]:
def populate_players_and_stats(db_path, seasons):
    """
    Populate players, skater_seasons, goalie_seasons, and player_teams tables.
    Skaters (A, D) go to skater_seasons, goalies (G) go to goalie_seasons.
    Uses the newly added stats from player.py Season class.
    """
    conn = sqlite3.connect(db_path)
    cursor = conn.cursor()
    
    players_added = set()
    skater_seasons_count = 0
    goalie_seasons_count = 0
    player_teams_count = 0
    
    for season in seasons:
        print(f"\n📅 Processing season {season}...")
        
        try:
            teams = get_season_teams(season)
            
            for team_abbrev in teams:
                try:
                    player_ids = get_all_player_ids(season, team_abbrev)
                    
                    for player_id in player_ids:
                        try:
                            # Load player data
                            player = load_player(player_id, seasons, '20252026')
                            
                            if not player:
                                continue
                            
                            # Insert player if not already added
                            if player_id not in players_added:
                                cursor.execute('''
                                INSERT OR IGNORE INTO players 
                                (player_id, first_name, last_name, full_name, position, role, birth_date,
                                 age, height, weight, country, salary)
                                VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
                                ''', (
                                    player.id,
                                    player.first_name,
                                    player.last_name,
                                    player.name,
                                    player.position,
                                    player.role,
                                    player.birth_date,
                                    player.age,
                                    player.height,
                                    player.weight,
                                    player.country,
                                    player.salary
                                ))
                                players_added.add(player_id)
                            
                            # Insert player-season stats (split by role)
                            if season in player.seasons:
                                season_data = player.seasons[season]
                                
                                if player.role == 'G':
                                    # Insert goalie stats using new attributes
                                    wins_per_game = None
                                    shutout_pct = None
                                    
                                    if season_data.n_games_played and season_data.n_games_played > 0:
                                        if season_data.n_wins:
                                            wins_per_game = season_data.n_wins / season_data.n_games_played
                                        if season_data.n_shutouts:
                                            shutout_pct = (season_data.n_shutouts / season_data.n_games_played) * 100
                                    
                                    cursor.execute('''
                                    INSERT OR IGNORE INTO goalie_seasons
                                    (player_id, season_id, games_played, games_started, wins, losses, ties,
                                     overtime_losses, shutouts, goals_against, goals_against_avg, shots_against,
                                     saves, save_pct, time_on_ice, penalty_minutes,
                                     goals, assists, points, wins_per_game, shutout_pct)
                                    VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
                                    ''', (
                                        player.id,
                                        season,
                                        season_data.n_games_played,
                                        season_data.n_games_started,
                                        season_data.n_wins,
                                        season_data.n_losses,
                                        season_data.n_ties,
                                        season_data.n_overtime_losses,
                                        season_data.n_shutouts,
                                        season_data.n_goals_against,
                                        season_data.n_goals_against_avg,
                                        season_data.n_shots_against,
                                        season_data.n_saves,
                                        season_data.n_save_percentage,
                                        season_data.n_time_on_ice,
                                        season_data.n_pim,
                                        season_data.n_goals,
                                        season_data.n_assists,
                                        season_data.n_points,
                                        wins_per_game,
                                        shutout_pct
                                    ))
                                    goalie_seasons_count += 1
                                
                                else:
                                    # Insert skater stats using new attributes
                                    points = None
                                    ppg = None
                                    m_points = None
                                    m_ppg = None
                                    goals_per_game = None
                                    assists_per_game = None
                                    shots_per_game = None
                                    
                                    if season_data.n_games_played and season_data.n_games_played > 0:
                                        if season_data.n_goals is not None and season_data.n_assists is not None:
                                            points = season_data.n_points
                                            ppg = points / season_data.n_games_played
                                            m_points = season_data.get_marqueur_points(player.role)
                                            m_ppg = season_data.get_ratio_marqueur_points(player.role)
                                            goals_per_game = season_data.n_goals / season_data.n_games_played
                                            assists_per_game = season_data.n_assists / season_data.n_games_played
                                        if season_data.n_shots:
                                            shots_per_game = season_data.n_shots / season_data.n_games_played
                                    
                                    cursor.execute('''
                                    INSERT OR IGNORE INTO skater_seasons
                                    (player_id, season_id, games_played, goals, assists, points,
                                     plus_minus, penalty_minutes, shots, shooting_pct, time_on_ice_per_game,
                                     powerplay_goals, powerplay_points, shorthanded_goals, shorthanded_points,
                                     game_winning_goals, overtime_goals, faceoff_pct, avg_shifts_per_game,
                                     ppg, goals_per_game, assists_per_game, shots_per_game, marqueur_points, marqueur_ppg)
                                    VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
                                    ''', (
                                        player.id,
                                        season,
                                        season_data.n_games_played,
                                        season_data.n_goals,
                                        season_data.n_assists,
                                        points,
                                        season_data.n_plus_minus,
                                        season_data.n_pim,
                                        season_data.n_shots,
                                        season_data.n_shooting_percentage,
                                        season_data.n_time_on_ice_per_game,
                                        season_data.n_powerplay_goals,
                                        season_data.n_powerplay_points,
                                        season_data.n_shorthanded_goals,
                                        season_data.n_shorthanded_points,
                                        season_data.n_game_winning_goals,
                                        season_data.n_overtime_goals,
                                        season_data.n_faceoff_percentage,
                                        season_data.n_avg_shifts_per_game,
                                        ppg,
                                        goals_per_game,
                                        assists_per_game,
                                        shots_per_game,
                                        m_points,
                                        m_ppg
                                    ))
                                    skater_seasons_count += 1
                            
                            # Insert player-team relationship
                            cursor.execute('SELECT team_id FROM teams WHERE team_abbrev = ?', (team_abbrev,))
                            result = cursor.fetchone()
                            if result:
                                team_id = result[0]
                                cursor.execute('''
                                INSERT OR IGNORE INTO player_teams
                                (player_id, team_id, season_id)
                                VALUES (?, ?, ?)
                                ''', (player.id, team_id, season))
                                player_teams_count += 1
                        
                        except Exception as e:
                            print(f"⚠️  Warning: Error processing player {player_id}: {e}")
                            continue
                
                except Exception as e:
                    print(f"⚠️  Warning: Could not get players for {team_abbrev}: {e}")
                    continue
        
        except Exception as e:
            print(f"⚠️  Warning: Could not process season {season}: {e}")
            continue
        
        # Commit after each season
        conn.commit()
        print(f"   Players: {len(players_added)}, Skater-seasons: {skater_seasons_count}, Goalie-seasons: {goalie_seasons_count}, Player-teams: {player_teams_count}")
    
    conn.close()
    
    print(f"\n✅ Database population complete!")
    print(f"   Total players: {len(players_added)}")
    print(f"   Total skater-season records: {skater_seasons_count}")
    print(f"   Total goalie-season records: {goalie_seasons_count}")
    print(f"   Total player-team relationships: {player_teams_count}")

# Populate the database
populate_players_and_stats(DB_NAME, SEASONS)

2025-10-06 23:42:56,569 - INFO - Player points data for 20002001 already exists, skipping download
2025-10-06 23:42:56,569 - INFO - Found 30 teams for season 20002001: ['PIT', 'COL', 'NJD', 'BOS', 'FLA', 'EDM', 'LAK', 'OTT', 'DAL', 'STL', 'WSH', 'BUF', 'NYR', 'PHI', 'DET', 'PHX', 'ATL', 'VAN', 'CHI', 'TOR', 'SJS', 'CGY', 'CAR', 'ANA', 'NYI', 'TBL', 'NSH', 'CBJ', 'MTL', 'MIN']
2025-10-06 23:42:56,574 - INFO - Team PIT data for 20002001 already exists, skipping download
2025-10-06 23:42:56,575 - INFO - Found 41 players (skaters + goalies) for team PIT in season 20002001
2025-10-06 23:42:56,575 - INFO - Player 8445428 data already exists, skipping download
2025-10-06 23:42:56,578 - INFO - Salary not found for player Bergevin, Marc, using default salary
2025-10-06 23:42:56,578 - INFO - Player 8446435 data already exists, skipping download
2025-10-06 23:42:56,578 - INFO - Salary not found for player Dollas, Bobby, using default salary
2025-10-06 23:42:56,582 - INFO - Player 8448208 data alr


📅 Processing season 20002001...


2025-10-06 23:42:56,733 - INFO - Player 8459538 data already exists, skipping download
2025-10-06 23:42:56,735 - INFO - Salary not found for player Pratt, Nolan, using default salary
2025-10-06 23:42:56,735 - INFO - Player 8459654 data already exists, skipping download
2025-10-06 23:42:56,739 - INFO - Salary not found for player Prpic, Joel, using default salary
2025-10-06 23:42:56,739 - INFO - Player 8460012 data already exists, skipping download
2025-10-06 23:42:56,744 - INFO - Salary not found for player Messier, Eric, using default salary
2025-10-06 23:42:56,745 - INFO - Player 8460254 data already exists, skipping download
2025-10-06 23:42:56,748 - INFO - Salary not found for player De Vries, Greg, using default salary
2025-10-06 23:42:56,749 - INFO - Player 8460509 data already exists, skipping download
2025-10-06 23:42:56,752 - INFO - Salary not found for player Dingman, Chris, using default salary
2025-10-06 23:42:56,753 - INFO - Player 8460562 data already exists, skipping dow

   Players: 973, Skater-seasons: 973, Goalie-seasons: 98, Player-teams: 1071

📅 Processing season 20012002...


2025-10-06 23:42:59,764 - INFO - Salary not found for player Allen, Bryan, using default salary
2025-10-06 23:42:59,765 - INFO - Player 8467359 data already exists, skipping download
2025-10-06 23:42:59,769 - INFO - Salary not found for player Chubarov, Artem, using default salary
2025-10-06 23:42:59,770 - INFO - Player 8467393 data already exists, skipping download
2025-10-06 23:42:59,773 - INFO - Salary not found for player Ruutu, Jarkko, using default salary
2025-10-06 23:42:59,775 - INFO - Player 8467851 data already exists, skipping download
2025-10-06 23:42:59,778 - INFO - Salary not found for player Kariya, Steven, using default salary
2025-10-06 23:42:59,779 - INFO - Player 8467875 data already exists, skipping download
2025-10-06 23:42:59,782 - INFO - Salary not found for player Sedin, Daniel, using default salary
2025-10-06 23:42:59,783 - INFO - Player 8467876 data already exists, skipping download
2025-10-06 23:42:59,787 - INFO - Salary not found for player Sedin, Henrik, us

...

   Players: 4142, Skater-seasons: 21402, Goalie-seasons: 2144, Player-teams: 23546

📅 Processing season 20232024...


2025-10-07 00:23:28,922 - INFO - Salary not found for player Foudy, Jean-Luc, using default salary
2025-10-07 00:23:28,922 - INFO - Player 8482712 data already exists, skipping download
2025-10-07 00:23:28,924 - INFO - Salary not found for player Olausson, Oskar, using default salary
2025-10-07 00:23:28,924 - INFO - Player 8483570 data already exists, skipping download
2025-10-07 00:23:28,926 - INFO - Salary not found for player Meyers, Ben, using default salary
2025-10-07 00:23:28,926 - INFO - Player 8484255 data already exists, skipping download
2025-10-07 00:23:28,929 - INFO - Salary not found for player Polin, Jason, using default salary
2025-10-07 00:23:28,930 - INFO - Player 8484258 data already exists, skipping download
2025-10-07 00:23:28,932 - INFO - Player 8484259 data already exists, skipping download
2025-10-07 00:23:28,935 - INFO - Salary not found for player Pavel, Ondrej, using default salary
2025-10-07 00:23:28,936 - INFO - Player 8480382 data already exists, skipping d

   Players: 4262, Skater-seasons: 22397, Goalie-seasons: 2245, Player-teams: 24642

📅 Processing season 20242025...


2025-10-07 00:23:31,841 - INFO - Player 8479442 data already exists, skipping download
2025-10-07 00:23:31,844 - INFO - Player 8480803 data already exists, skipping download
2025-10-07 00:23:31,847 - INFO - Player 8480834 data already exists, skipping download
2025-10-07 00:23:31,849 - INFO - Player 8481491 data already exists, skipping download
2025-10-07 00:23:31,851 - INFO - Player 8481617 data already exists, skipping download
2025-10-07 00:23:31,855 - INFO - Player 8483512 data already exists, skipping download
2025-10-07 00:23:31,857 - INFO - Salary not found for player Savoie, Matt, using default salary
2025-10-07 00:23:31,858 - INFO - Player 8485511 data already exists, skipping download
2025-10-07 00:23:31,860 - INFO - Salary not found for player Hutson, Quinn, using default salary
2025-10-07 00:23:31,860 - INFO - Player 8475717 data already exists, skipping download
2025-10-07 00:23:31,863 - INFO - Player 8479973 data already exists, skipping download
2025-10-07 00:23:31,866 

   Players: 4376, Skater-seasons: 23127, Goalie-seasons: 2322, Player-teams: 25449

📅 Processing season 20252026...
   Players: 4376, Skater-seasons: 23127, Goalie-seasons: 2322, Player-teams: 25449

✅ Database population complete!
   Total players: 4376
   Total skater-season records: 23127
   Total goalie-season records: 2322
   Total player-team relationships: 25449


## 6. Populate Team Standings

In [12]:
from data_download import download_season_data


def populate_team_standings(db_path, seasons):
    """
    Populate team standings from standings JSON files
    """
    conn = sqlite3.connect(db_path)
    cursor = conn.cursor()
    
    standings_count = 0
    
    for season in seasons:
        download_season_data(season)  # Ensure data is downloaded
    
        standings_file = config.data.get_standings_path(season)
        
        if not standings_file.exists():
            print(f"⚠️  Standings file not found for {season}")
            continue
        
        try:
            with open(standings_file, 'r', encoding='utf-8') as f:
                standings_data = json.load(f)
            
            # Parse standings data (structure may vary)
            if 'standings' in standings_data:
                for team_data in standings_data['standings']:
                    team_abbrev = team_data.get('teamAbbrev', {}).get('default', '')
                    
                    # Get team_id
                    cursor.execute('SELECT team_id FROM teams WHERE team_abbrev = ?', (team_abbrev,))
                    result = cursor.fetchone()
                    
                    if result:
                        team_id = result[0]
                        
                        cursor.execute('''
                        INSERT OR IGNORE INTO team_standings
                        (team_id, season_id, games_played, wins, losses, overtime_losses,
                         points, points_pct, goals_for, goals_against, goal_differential)
                        VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
                        ''', (
                            team_id,
                            season,
                            team_data.get('gamesPlayed', 0),
                            team_data.get('wins', 0),
                            team_data.get('losses', 0),
                            team_data.get('otLosses', 0),
                            team_data.get('points', 0),
                            team_data.get('pointPctg', 0.0),
                            team_data.get('goalFor', 0),
                            team_data.get('goalAgainst', 0),
                            team_data.get('goalDifferential', 0)
                        ))
                        standings_count += 1
        
        except Exception as e:
            print(f"⚠️  Error processing standings for {season}: {e}")
    
    conn.commit()
    conn.close()
    
    print(f"✅ Added {standings_count} team standings records")

populate_team_standings(DB_NAME, SEASONS)

2025-10-07 00:33:01,441 - INFO - Starting complete data download for season 20002001
2025-10-07 00:33:01,441 - INFO - Player points data for 20002001 already exists, skipping download
2025-10-07 00:33:01,441 - INFO - Downloading season standings for 20002001 (attempt 1/3)
2025-10-07 00:33:01,860 - INFO - Successfully downloaded season standings for 20002001
2025-10-07 00:33:02,865 - INFO - Player points data for 20002001 already exists, skipping download
2025-10-07 00:33:02,866 - INFO - Found 30 teams for season 20002001: ['PIT', 'COL', 'NJD', 'BOS', 'FLA', 'EDM', 'LAK', 'OTT', 'DAL', 'STL', 'WSH', 'BUF', 'NYR', 'PHI', 'DET', 'PHX', 'ATL', 'VAN', 'CHI', 'TOR', 'SJS', 'CGY', 'CAR', 'ANA', 'NYI', 'TBL', 'NSH', 'CBJ', 'MTL', 'MIN']
2025-10-07 00:33:02,866 - INFO - Starting download of 30 teams for season 20002001
2025-10-07 00:33:02,866 - INFO - Processing team 1/30: PIT
2025-10-07 00:33:02,866 - INFO - Team PIT data for 20002001 already exists, skipping download
2025-10-07 00:33:02,873 -

⚠️  Standings file not found for 20042005


2025-10-07 00:33:11,378 - INFO - Successfully downloaded season standings for 20052006
2025-10-07 00:33:12,380 - INFO - Player points data for 20052006 already exists, skipping download
2025-10-07 00:33:12,380 - INFO - Found 30 teams for season 20052006: ['SJS', 'NYR', 'WSH', 'OTT', 'PIT', 'CAR', 'ATL', 'TBL', 'ANA', 'NJD', 'FLA', 'COL', 'DET', 'NSH', 'PHI', 'MIN', 'VAN', 'TOR', 'DAL', 'EDM', 'BOS', 'BUF', 'CGY', 'LAK', 'NYI', 'PHX', 'MTL', 'CBJ', 'CHI', 'STL']
2025-10-07 00:33:12,380 - INFO - Starting download of 30 teams for season 20052006
2025-10-07 00:33:12,380 - INFO - Processing team 1/30: SJS
2025-10-07 00:33:12,380 - INFO - Team SJS data for 20052006 already exists, skipping download
2025-10-07 00:33:12,380 - INFO - Processing team 2/30: NYR
2025-10-07 00:33:12,380 - INFO - Team NYR data for 20052006 already exists, skipping download
2025-10-07 00:33:12,380 - INFO - Processing team 3/30: WSH
2025-10-07 00:33:12,380 - INFO - Team WSH data for 20052006 already exists, skipping d

✅ Added 63 team standings records


## 7. Database Summary and Verification

In [8]:
def get_database_summary(db_path):
    """
    Get summary statistics about the database
    """
    conn = sqlite3.connect(db_path)
    
    print("="*60)
    print("DATABASE SUMMARY")
    print("="*60)
    
    # Table counts
    tables = ['players', 'teams', 'seasons', 'skater_seasons', 'goalie_seasons', 'player_teams', 'team_standings']
    
    for table in tables:
        count = pd.read_sql_query(f"SELECT COUNT(*) as count FROM {table}", conn)['count'][0]
        print(f"{table:20s}: {count:6d} records")
    
    # Player breakdown by role
    print("\n" + "="*60)
    print("PLAYER BREAKDOWN")
    print("="*60)
    role_counts = pd.read_sql_query("SELECT role, COUNT(*) as count FROM players GROUP BY role", conn)
    for _, row in role_counts.iterrows():
        role_name = {'A': 'Attackers', 'D': 'Defensemen', 'G': 'Goalies'}.get(row['role'], row['role'])
        print(f"{role_name:20s}: {row['count']:6d} players")
    
    print("\n" + "="*60)
    print("SAMPLE QUERIES")
    print("="*60)
    
    # Sample: Top scorers from a season (skaters)
    print("\n📊 Top 10 Skaters (20232024):")
    query = '''
    SELECT p.full_name, p.position, ss.goals, ss.assists, ss.points, ss.ppg
    FROM skater_seasons ss
    JOIN players p ON ss.player_id = p.player_id
    WHERE ss.season_id = '20232024' AND ss.points IS NOT NULL
    ORDER BY ss.points DESC
    LIMIT 10
    '''
    df = pd.read_sql_query(query, conn)
    print(df.to_string(index=False))
    
    # Sample: Top goalies from a season
    print("\n🥅 Top 10 Goalies (20232024):")
    query = '''
    SELECT p.full_name, gs.games_played, gs.wins, gs.shutouts, 
           gs.goals_against_avg, gs.save_pct
    FROM goalie_seasons gs
    JOIN players p ON gs.player_id = p.player_id
    WHERE gs.season_id = '20232024' AND gs.games_played >= 10
    ORDER BY gs.save_pct DESC
    LIMIT 10
    '''
    df = pd.read_sql_query(query, conn)
    print(df.to_string(index=False))
    
    conn.close()

get_database_summary(DB_NAME)

DATABASE SUMMARY
players             :   4376 records
teams               :     35 records
seasons             :     26 records
skater_seasons      :  21285 records
goalie_seasons      :   2207 records
player_teams        :  25449 records
team_standings      :     63 records

PLAYER BREAKDOWN
Attackers           :   2601 players
Defensemen          :   1332 players
Goalies             :    443 players

SAMPLE QUERIES

📊 Top 10 Skaters (20232024):
       full_name position  goals  assists  points      ppg
 Nikita Kucherov        R     44      100     144 1.777778
Nathan MacKinnon        C     51       89     140 1.707317
  Connor McDavid        C     32      100     132 1.736842
  Artemi Panarin        L     49       71     120 1.463415
  David Pastrnak        R     47       63     110 1.341463
 Auston Matthews        C     69       38     107 1.320988
  Leon Draisaitl        C     41       65     106 1.308642
  Mikko Rantanen        R     42       62     104 1.300000
     J.T. Miller  

## 8. Example Query Functions

In [9]:
# Example: Get all seasons for a specific player (handles both skaters and goalies)
def get_player_career(player_name):
    conn = sqlite3.connect(DB_NAME)
    
    # First check if player is a goalie or skater
    role_query = "SELECT role FROM players WHERE full_name LIKE ? LIMIT 1"
    role_result = pd.read_sql_query(role_query, conn, params=(f'%{player_name}%',))
    
    if role_result.empty:
        conn.close()
        return pd.DataFrame()
    
    role = role_result['role'][0]
    
    if role == 'G':
        # Query for goalies
        query = '''
        SELECT p.full_name, p.position, s.season_id, 
               gs.games_played, gs.wins, gs.shutouts, gs.goals_against_avg, gs.save_pct,
               t.team_abbrev
        FROM players p
        JOIN goalie_seasons gs ON p.player_id = gs.player_id
        JOIN seasons s ON gs.season_id = s.season_id
        LEFT JOIN player_teams pt ON p.player_id = pt.player_id AND s.season_id = pt.season_id
        LEFT JOIN teams t ON pt.team_id = t.team_id
        WHERE p.full_name LIKE ?
        ORDER BY s.season_id
        '''
    else:
        # Query for skaters
        query = '''
        SELECT p.full_name, p.position, s.season_id, 
               ss.games_played, ss.goals, ss.assists, ss.points, ss.ppg,
               t.team_abbrev
        FROM players p
        JOIN skater_seasons ss ON p.player_id = ss.player_id
        JOIN seasons s ON ss.season_id = s.season_id
        LEFT JOIN player_teams pt ON p.player_id = pt.player_id AND s.season_id = pt.season_id
        LEFT JOIN teams t ON pt.team_id = t.team_id
        WHERE p.full_name LIKE ?
        ORDER BY s.season_id
        '''
    
    df = pd.read_sql_query(query, conn, params=(f'%{player_name}%',))
    conn.close()
    return df

# Example: Get team performance across seasons
def get_team_performance(team_abbrev):
    conn = sqlite3.connect(DB_NAME)
    query = '''
    SELECT s.season_id, t.team_abbrev,
           ts.games_played, ts.wins, ts.losses, ts.points, ts.points_pct,
           ts.goals_for, ts.goals_against, ts.goal_differential
    FROM team_standings ts
    JOIN teams t ON ts.team_id = t.team_id
    JOIN seasons s ON ts.season_id = s.season_id
    WHERE t.team_abbrev = ?
    ORDER BY s.season_id
    '''
    df = pd.read_sql_query(query, conn, params=(team_abbrev,))
    conn.close()
    return df

# Example: Get top skaters by position and minimum games
def get_top_skaters_by_position(position, min_games=20, season='20232024'):
    conn = sqlite3.connect(DB_NAME)
    query = '''
    SELECT p.full_name, p.position, p.role, 
           ss.games_played, ss.goals, ss.assists, ss.points, ss.ppg,
           t.team_abbrev
    FROM players p
    JOIN skater_seasons ss ON p.player_id = ss.player_id
    LEFT JOIN player_teams pt ON p.player_id = pt.player_id AND ss.season_id = pt.season_id
    LEFT JOIN teams t ON pt.team_id = t.team_id
    WHERE p.role = ? AND ss.season_id = ? AND ss.games_played >= ?
    ORDER BY ss.ppg DESC
    LIMIT 20
    '''
    df = pd.read_sql_query(query, conn, params=(position, season, min_games))
    conn.close()
    return df

# Example: Get top goalies by save percentage
def get_top_goalies(min_games=10, season='20232024'):
    conn = sqlite3.connect(DB_NAME)
    query = '''
    SELECT p.full_name, p.position,
           gs.games_played, gs.wins, gs.shutouts, 
           gs.goals_against_avg, gs.save_pct,
           t.team_abbrev
    FROM players p
    JOIN goalie_seasons gs ON p.player_id = gs.player_id
    LEFT JOIN player_teams pt ON p.player_id = pt.player_id AND gs.season_id = pt.season_id
    LEFT JOIN teams t ON pt.team_id = t.team_id
    WHERE gs.season_id = ? AND gs.games_played >= ?
    ORDER BY gs.save_pct DESC
    LIMIT 20
    '''
    df = pd.read_sql_query(query, conn, params=(season, min_games))
    conn.close()
    return df

print("📋 Example query functions defined:")
print("  - get_player_career(player_name) - handles both skaters and goalies")
print("  - get_team_performance(team_abbrev)")
print("  - get_top_skaters_by_position(position, min_games, season)")
print("  - get_top_goalies(min_games, season)")
print("\nTry them out below!")

📋 Example query functions defined:
  - get_player_career(player_name) - handles both skaters and goalies
  - get_team_performance(team_abbrev)
  - get_top_skaters_by_position(position, min_games, season)
  - get_top_goalies(min_games, season)

Try them out below!


In [10]:
# Example usage: Top attackers from 2023-24 season
print("🏆 Top 10 Attackers (2023-24):")
df = get_top_skaters_by_position('A', min_games=20, season='20232024')
print(df)

print("\n🥅 Top 10 Goalies (2023-24):")
df = get_top_goalies(min_games=10, season='20232024')
print(df)

🏆 Top 10 Attackers (2023-24):
            full_name position role  games_played  goals  assists  points  \
0     Nikita Kucherov        R    A            81     44      100     144   
1      Connor McDavid        C    A            76     32      100     132   
2    Nathan MacKinnon        C    A            82     51       89     140   
3      Artemi Panarin        L    A            82     49       71     120   
4      David Pastrnak        R    A            82     47       63     110   
5     Auston Matthews        C    A            81     69       38     107   
6      Leon Draisaitl        C    A            81     41       65     106   
7      Mikko Rantanen        R    A            80     42       62     104   
8     Kirill Kaprizov        L    A            75     46       50      96   
9         J.T. Miller        C    A            81     37       66     103   
10       Mitch Marner        R    A            69     26       59      85   
11   William Nylander        R    A           

## 9. Export Database Info

In [11]:
# Export database schema to text file
conn = sqlite3.connect(DB_NAME)
cursor = conn.cursor()

with open('database_schema.sql', 'w') as f:
    for line in conn.iterdump():
        if line.startswith('CREATE TABLE') or line.startswith('CREATE INDEX'):
            f.write(line + '\n')

conn.close()

print("✅ Database schema exported to 'database_schema.sql'")
print(f"✅ Database file: {DB_NAME}")
print(f"\n🎉 NHL Database creation complete!")
print(f"\n📊 Database Structure:")
print(f"   - Skaters stats in 'skater_seasons' table (with all new stats)")
print(f"   - Goalie stats in 'goalie_seasons' table (with all new stats)")
print(f"   - All players in 'players' table (role: A/D/G)")
print(f"\nYou can now query the database using SQL or pandas.read_sql_query()")

✅ Database schema exported to 'database_schema.sql'
✅ Database file: nhl_data.db

🎉 NHL Database creation complete!

📊 Database Structure:
   - Skaters stats in 'skater_seasons' table (with all new stats)
   - Goalie stats in 'goalie_seasons' table (with all new stats)
   - All players in 'players' table (role: A/D/G)

You can now query the database using SQL or pandas.read_sql_query()
